In [2]:
!pip install pytorch-lightning

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 832.4/832.4 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 983.2/983.2 kB 38.6 MB/s eta 0:00:00


In [3]:
!pip install wandb

In [7]:
# ============================================
# EXPERIMENTO: Comparación de optimizadores
# Dataset: Moons (clasificación no lineal)
# Modelo: MLP 3 capas
# ============================================

In [8]:
import torch
from torch import nn
from torch.utils.data import DataLoader, TensorDataset, random_split
import torch.nn.functional as F
from sklearn.datasets import make_moons
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
import pytorch_lightning as pl
from pytorch_lightning.loggers import WandbLogger
import wandb

In [9]:
# --------------------------------------------
# (1) Dataset
# --------------------------------------------
X, y = make_moons(n_samples=2000, noise=0.2, random_state=42)
scaler = StandardScaler()
X = scaler.fit_transform(X)
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.2, random_state=42)

train_ds = TensorDataset(torch.tensor(X_train, dtype=torch.float32),
                         torch.tensor(y_train, dtype=torch.long))
val_ds = TensorDataset(torch.tensor(X_val, dtype=torch.float32),
                       torch.tensor(y_val, dtype=torch.long))

In [10]:
# --------------------------------------------
# (2) Modelo base
# --------------------------------------------
class MLP(pl.LightningModule):
    def __init__(self, optimizer_name="adam", lr=1e-3):
        super().__init__()
        self.optimizer_name = optimizer_name
        self.lr = lr

        self.model = nn.Sequential(
            nn.Linear(2, 64),
            nn.ReLU(),
            nn.Linear(64, 64),
            nn.ReLU(),
            nn.Linear(64, 2)
        )
        self.save_hyperparameters()

    def forward(self, x):
        return self.model(x)

    def training_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        acc = (logits.argmax(dim=1) == y).float().mean()
        self.log("train_loss", loss)
        self.log("train_acc", acc, prog_bar=True)
        return loss

    def validation_step(self, batch, batch_idx):
        x, y = batch
        logits = self(x)
        loss = F.cross_entropy(logits, y)
        acc = (logits.argmax(dim=1) == y).float().mean()
        self.log("val_loss", loss, prog_bar=True)
        self.log("val_acc", acc, prog_bar=True)
        return loss

    def configure_optimizers(self):
        if self.optimizer_name.lower() == "adam":
            return torch.optim.Adam(self.parameters(), lr=self.lr)
        elif self.optimizer_name.lower() == "adamw":
            return torch.optim.AdamW(self.parameters(), lr=self.lr)
        elif self.optimizer_name.lower() == "rmsprop":
            return torch.optim.RMSprop(self.parameters(), lr=self.lr)
        elif self.optimizer_name.lower() == "sgd":
            return torch.optim.SGD(self.parameters(), lr=self.lr, momentum=0.9)
        else:
            raise ValueError(f"Unknown optimizer: {self.optimizer_name}")

In [14]:
# --------------------------------------------
# (3) Entrenamiento
# --------------------------------------------
def train_experiment(optimizer_name="adam", lr=1e-3, use_wandb=False):
    if use_wandb:
        wandb.login()
        wandb_logger = WandbLogger(project="comparacion_optimizers", name=f"{optimizer_name}_lr{lr}")
        wandb_logger = WandbLogger(
          project="comparacion_optimizers",
          name=f"{optimizer_name}_lr{lr}",
          id=f"{optimizer_name}_run",
          reinit=True  # ensures a new run object each time
       )

    else:
        wandb_logger = None

    model = MLP(optimizer_name=optimizer_name, lr=lr)

    train_loader = DataLoader(train_ds, batch_size=64, shuffle=True)
    val_loader = DataLoader(val_ds, batch_size=64)

    trainer = pl.Trainer(
        max_epochs=50,
        logger=wandb_logger,
        log_every_n_steps=10,
        accelerator="auto",
        enable_progress_bar=True,
    )
    trainer.fit(model, train_loader, val_loader)

In [15]:
# --------------------------------------------
# (4) Ejecutar comparaciones
# --------------------------------------------
if __name__ == "__main__":
    for opt in ["adam", "adamw", "rmsprop", "sgd"]:
        train_experiment(optimizer_name=opt, lr=1e-3, use_wandb=True)
        wandb.finish()

wandb: WARNING Calling wandb.login() after wandb.init() has no effect.
INFO:pytorch_lightning.utilities.rank_zero:💡 Tip: For seamless cloud uploads and versioning, try installing [litmodels](https://pypi.org/project/litmodels/) to enable LitModelCheckpoint, which syncs automatically with the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.callbacks.model_summary:
  | Name  | Type       | Params | Mode 
---------------------------------------------
0 | model | Sequential | 4.5 K  | train
---------------------------------------------
4.5 K     Trainable params
0         Non-trainable params
4.5 K     Total params
0.018     Total estimated model params size (MB)
6         Modules in train mode
0         Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:`Trainer.fit` stopped: `max_epochs=50` reached.


In [4]:
import pytorch_lightning as pl
from pytorch_lightning.loggers import WandbLogger
import wandb

In [6]:
# Inicia sesión
wandb.login()

# Crea el logger
wandb_logger = WandbLogger(project="comparacion_optimizadores", name="adam_vs_adamw")

# Ejemplo de modelo Lightning
trainer = pl.Trainer(
    max_epochs=20,
    logger=wandb_logger,
    log_every_n_steps=10,
)

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: gdmk to https://api.wandb.ai. Use `wandb login --relogin` to force relogin
INFO:pytorch_lightning.utilities.rank_zero:💡 Tip: For seamless cloud uploads and versioning, try installing [litmodels](https://pypi.org/project/litmodels/) to enable LitModelCheckpoint, which syncs automatically with the Lightning model registry.
INFO:pytorch_lightning.utilities.rank_zero:GPU available: False, used: False
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
